Team Members

*   Libin Kutty - Group 2
*   Ritu Gahir - Group 3
*   Viju Sudhi - Group 10



In [0]:
%tensorflow_version 2.x

In [2]:
import tensorflow as tf
print(tf.__version__)

2.2.0-rc4


In [3]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive


In [4]:
!ls "/content/drive/My Drive/Colab Notebook/IDL/"

datasets.py		IDL_Assingnment_1.ipynb  __pycache__	Trail.ipynb
IDL_Assignment_2.ipynb	linear_tb.ipynb		 tf_data.ipynb
IDL_Assignment_3.ipynb	mlp_keras.ipynb		 trail


In [5]:
import os
print(os.getcwd())
os.chdir("/content/drive/My Drive/Colab Notebook/IDL")
print(os.getcwd())

/content
/content/drive/My Drive/Colab Notebook/IDL


In [0]:
import numpy as np
import matplotlib.pyplot as plt
from datasets import MNISTDataset
import time

In [7]:
(train_imgs, train_lbls), (test_imgs, test_lbls) = tf.keras.datasets.mnist.load_data()
mnist = MNISTDataset(train_imgs.reshape((-1, 784)), train_lbls,
                     test_imgs.reshape((-1, 784)), test_lbls,
                     batch_size=256, seed=int(time.time()))

11493376/11490434 [==============================] - 0s 0us/step


Fail 1


It can be seen that the loss, weight and gradient value are been displayed as NaN which means that we have a problem of exploding gradient. which can be solved by rather decreasing the weights or decreasing the hidden layer.

In [8]:

logdir = os.path.join("logs", "fail" + str(time.time()))
train_writer = tf.summary.create_file_writer(os.path.join(logdir, "train"))
test_writer = tf.summary.create_file_writer(os.path.join(logdir, "test"))

# define the model first, from input to output

# this is a super deep model, cool!
n_units = 100
n_layers = 8
w_range = 0.4

# just set up a "chain" of hidden layers
layers = []
for layer in range(n_layers):
    layers.append(tf.keras.layers.Dense(
        n_units, activation=tf.nn.relu,
        kernel_initializer=tf.initializers.RandomUniform(minval=-w_range,
                                                         maxval=w_range),
        bias_initializer=tf.initializers.constant(0.001)))

# finally add the output layer
layers.append(tf.keras.layers.Dense(
    10, kernel_initializer=tf.initializers.RandomUniform(minval=-w_range,
                                                         maxval=w_range)))

lr = 0.1
for step in range(2000):
    img_batch, lbl_batch = mnist.next_batch()
    with tf.GradientTape() as tape:
        # here we just run all the layers in sequence via a for-loop
        out = img_batch
        for layer in layers:
            out = layer(out)
        xent = tf.reduce_mean(tf.nn.sparse_softmax_cross_entropy_with_logits(
            logits=out, labels=lbl_batch))

    weights = [var for l in layers for var in l.trainable_variables]
    grads = tape.gradient(xent, weights)
    for grad, var in zip(grads, weights):
        var.assign_sub(lr*grad)

    with train_writer.as_default():
      tf.summary.histogram("Logits", out, step=step)
      tf.summary.histogram("Gradient_0", tf.norm(grads[0]), step=step)
      tf.summary.histogram("Gradient_8", tf.norm(grads[8]), step=step)
      tf.summary.histogram("Weights_0", weights[0], step=step)
      tf.summary.histogram("Weights_8", weights[8], step=step)

    if not step % 100:
        preds = tf.argmax(out, axis=1, output_type=tf.int32)
        acc = tf.reduce_mean(tf.cast(tf.equal(preds, lbl_batch), tf.float32))
        print("Loss: {} Accuracy: {}".format(xent, acc))
        with train_writer.as_default():
          tf.summary.scalar("Gradient_Scalar", tf.norm(grads[0]), step=step)
          tf.summary.scalar("Loss", xent, step=step)
          tf.summary.scalar("Accuracy", acc, step=step)
          tf.summary.image("Input", tf.reshape(img_batch, [-1, 28, 28, 1]), step=step)

out = mnist.test_data
for layer in layers:
    out = layer(out)
test_preds = tf.argmax(out, axis=1, output_type=tf.int32)
acc = tf.reduce_mean(tf.cast(tf.equal(test_preds, mnist.test_labels), tf.float32))
print("Final test accuracy: {}".format(acc))


Loss: 148.93618774414062 Accuracy: 0.09765625
Loss: nan Accuracy: 0.11328125
Loss: nan Accuracy: 0.09765625
Starting new epoch...
Loss: nan Accuracy: 0.0859375
Loss: nan Accuracy: 0.08203125
Starting new epoch...
Loss: nan Accuracy: 0.125
Loss: nan Accuracy: 0.0703125
Loss: nan Accuracy: 0.11328125
Starting new epoch...
Loss: nan Accuracy: 0.09765625
Loss: nan Accuracy: 0.10546875
Starting new epoch...
Loss: nan Accuracy: 0.1015625
Loss: nan Accuracy: 0.1015625
Starting new epoch...
Loss: nan Accuracy: 0.0625
Loss: nan Accuracy: 0.1015625
Loss: nan Accuracy: 0.11328125
Starting new epoch...
Loss: nan Accuracy: 0.125
Loss: nan Accuracy: 0.12890625
Starting new epoch...
Loss: nan Accuracy: 0.109375
Loss: nan Accuracy: 0.109375
Starting new epoch...
Loss: nan Accuracy: 0.1015625
Final test accuracy: 0.09799999743700027


Fail 2

Due to vanishing gradient problem, weights are not getting updated as there are 8 hidden layers with sigmoid function, gradients keep on decreasing. So to solve this we can either reduce the number of layer or change the activation functionn to ReLU.

In [9]:
logdir = os.path.join("logs", "fail" + str(time.time()))
train_writer = tf.summary.create_file_writer(os.path.join(logdir, "train"))
test_writer = tf.summary.create_file_writer(os.path.join(logdir, "test"))

# define the model first, from input to output

# this is a super deep model, cool!
n_units = 100
n_layers = 8
w_range = 0.1

# just set up a "chain" of hidden layers
layers = []
for layer in range(n_layers):
    layers.append(tf.keras.layers.Dense(
        n_units, activation=tf.nn.sigmoid,
        kernel_initializer=tf.initializers.RandomUniform(minval=-w_range,
                                                         maxval=w_range),
        bias_initializer=tf.initializers.constant(0.001)))

# finally add the output layer
layers.append(tf.keras.layers.Dense(
    10, kernel_initializer=tf.initializers.RandomUniform(minval=-w_range,
                                                         maxval=w_range)))

lr = 0.1
for step in range(2000):
    img_batch, lbl_batch = mnist.next_batch()
    with tf.GradientTape() as tape:
        # here we just run all the layers in sequence via a for-loop
        out = img_batch
        for layer in layers:
            out = layer(out)
        xent = tf.reduce_mean(tf.nn.sparse_softmax_cross_entropy_with_logits(
            logits=out, labels=lbl_batch))

    weights = [var for l in layers for var in l.trainable_variables]
    grads = tape.gradient(xent, weights)
    for grad, var in zip(grads, weights):
        var.assign_sub(lr*grad)

    with train_writer.as_default():
      tf.summary.histogram("Logits", out, step=step)
      tf.summary.histogram("Weights_0", weights[0], step=step)
      tf.summary.histogram("Weights_8", weights[8], step=step)
      tf.summary.histogram("Gradient_0", tf.norm(grads[0]), step=step)
      tf.summary.histogram("Gradient_8", tf.norm(grads[8]), step=step)

    if not step % 100:
        preds = tf.argmax(out, axis=1, output_type=tf.int32)
        acc = tf.reduce_mean(tf.cast(tf.equal(preds, lbl_batch), tf.float32))
        print("Loss: {} Accuracy: {}".format(xent, acc))
        with train_writer.as_default():
          tf.summary.scalar("Gradient Scalar", tf.norm(grads[0]), step=step)          
          tf.summary.scalar("Loss", xent, step=step)
          tf.summary.scalar("Accuracy", acc, step=step)
          tf.summary.image("input", tf.reshape(img_batch, [-1, 28, 28, 1]), step=step)


out = mnist.test_data
for layer in layers:
    out = layer(out)
test_preds = tf.argmax(out, axis=1, output_type=tf.int32)
acc = tf.reduce_mean(tf.cast(tf.equal(test_preds, mnist.test_labels), tf.float32))
print("Final test accuracy: {}".format(acc))


Loss: 2.3452627658843994 Accuracy: 0.08984375
Loss: 2.299091100692749 Accuracy: 0.08984375
Starting new epoch...
Loss: 2.3039069175720215 Accuracy: 0.08984375
Loss: 2.296029567718506 Accuracy: 0.09375
Starting new epoch...
Loss: 2.304856300354004 Accuracy: 0.109375
Loss: 2.306776523590088 Accuracy: 0.0859375
Starting new epoch...
Loss: 2.2958390712738037 Accuracy: 0.109375
Loss: 2.2926087379455566 Accuracy: 0.109375
Loss: 2.3035497665405273 Accuracy: 0.1171875
Starting new epoch...
Loss: 2.298847198486328 Accuracy: 0.14453125
Loss: 2.303607940673828 Accuracy: 0.09765625
Starting new epoch...
Loss: 2.3048949241638184 Accuracy: 0.07421875
Loss: 2.307506561279297 Accuracy: 0.10546875
Starting new epoch...
Loss: 2.3169689178466797 Accuracy: 0.08203125
Loss: 2.299983263015747 Accuracy: 0.15234375
Loss: 2.3052196502685547 Accuracy: 0.10546875
Starting new epoch...
Loss: 2.3005809783935547 Accuracy: 0.08203125
Loss: 2.307116985321045 Accuracy: 0.08984375
Starting new epoch...
Loss: 2.30758404

Fail 3

The range of the weight is from -0.01 to 0 and the activation function is relu which will give 0 for negative value. Since the weights are very less and also in negative, the output of this will be mostly 0. We can confirm this with the logits graph as they are in the range of -0.1 to 0.1 and mostly 0. So to solve this we should increase the range of weights to have some positive value as well.

In [10]:

logdir = os.path.join("logs", "fail" + str(time.time()))
train_writer = tf.summary.create_file_writer(os.path.join(logdir, "train"))
test_writer = tf.summary.create_file_writer(os.path.join(logdir, "test"))

# define the model first, from input to output

# let's use fewer layers...
n_units = 100
n_layers = 2

# just set up a "chain" of hidden layers
layers = []
for layer in range(n_layers):
    layers.append(tf.keras.layers.Dense(
        n_units, activation=tf.nn.relu,
        kernel_initializer=tf.initializers.RandomUniform(minval=-0.01,
                                                         maxval=0.),
        bias_initializer=tf.initializers.constant(0.001)))

# finally add the output layer
layers.append(tf.keras.layers.Dense(
    10, kernel_initializer=tf.initializers.RandomUniform(minval=-0.01,
                                                         maxval=0.01)))

lr = 0.1
for step in range(2000):
    img_batch, lbl_batch = mnist.next_batch()
    with tf.GradientTape() as tape:
        # here we just run all the layers in sequence via a for-loop
        out = img_batch
        for layer in layers:
            out = layer(out)
        xent = tf.reduce_mean(tf.nn.sparse_softmax_cross_entropy_with_logits(
            logits=out, labels=lbl_batch))

    weights = [var for l in layers for var in l.trainable_variables]
    grads = tape.gradient(xent, weights)
    for grad, var in zip(grads, weights):
        var.assign_sub(lr*grad)

    with train_writer.as_default():
      tf.summary.histogram("Logits", out, step=step)
      tf.summary.histogram("Weights_0", weights[0], step=step)
      tf.summary.histogram("Weights_2", weights[2], step=step)
      tf.summary.histogram("Gradient_0", tf.norm(grads[0]), step=step)
      tf.summary.histogram("Gradient_2", tf.norm(grads[2]), step=step)

    if not step % 100:
        preds = tf.argmax(out, axis=1, output_type=tf.int32)
        acc = tf.reduce_mean(tf.cast(tf.equal(preds, lbl_batch), tf.float32))
        print("Loss: {} Accuracy: {}".format(xent, acc))
        with train_writer.as_default():
          tf.summary.scalar("Gradient Scalar", tf.norm(grads[0]), step=step)
          tf.summary.scalar("Loss", xent, step=step)
          tf.summary.scalar("Accuracy", acc, step=step)
          tf.summary.image("input", tf.reshape(img_batch, [-1, 28, 28, 1]), step=step)


out = mnist.test_data
for layer in layers:
    out = layer(out)
test_preds = tf.argmax(out, axis=1, output_type=tf.int32)
acc = tf.reduce_mean(tf.cast(tf.equal(test_preds, mnist.test_labels), tf.float32))
print("Final test accuracy: {}".format(acc))


Loss: 2.3025851249694824 Accuracy: 0.078125
Loss: 2.3036844730377197 Accuracy: 0.08984375
Loss: 2.300999879837036 Accuracy: 0.1171875
Starting new epoch...
Loss: 2.3052597045898438 Accuracy: 0.08984375
Loss: 2.3039956092834473 Accuracy: 0.109375
Starting new epoch...
Loss: 2.299206256866455 Accuracy: 0.12890625
Loss: 2.305536985397339 Accuracy: 0.1015625
Starting new epoch...
Loss: 2.3060359954833984 Accuracy: 0.09375
Loss: 2.303772449493408 Accuracy: 0.12109375
Loss: 2.3020734786987305 Accuracy: 0.10546875
Starting new epoch...
Loss: 2.298429012298584 Accuracy: 0.12109375
Loss: 2.2934961318969727 Accuracy: 0.15625
Starting new epoch...
Loss: 2.304945945739746 Accuracy: 0.05859375
Loss: 2.300503730773926 Accuracy: 0.140625
Loss: 2.3045759201049805 Accuracy: 0.109375
Starting new epoch...
Loss: 2.298243999481201 Accuracy: 0.125
Loss: 2.299220085144043 Accuracy: 0.09765625
Starting new epoch...
Loss: 2.3044538497924805 Accuracy: 0.09765625
Loss: 2.296980142593384 Accuracy: 0.15234375
Sta

Fail 4

Problem with this code is that the images are full of noise. We can see that in the image.
After removing noise, the model architecture works well.

In [11]:

logdir = os.path.join("logs", "fail" + str(time.time()))
train_writer = tf.summary.create_file_writer(os.path.join(logdir, "train"))
test_writer = tf.summary.create_file_writer(os.path.join(logdir, "test"))

# define the model first, from input to output

# let's use fewer layers...
n_units = 100
n_layers = 2

# just set up a "chain" of hidden layers
layers = []
for layer in range(n_layers):
    layers.append(tf.keras.layers.Dense(
        n_units, activation=tf.nn.relu,
        kernel_initializer=tf.initializers.RandomUniform(minval=-0.01,
                                                         maxval=0.01),
        bias_initializer=tf.initializers.constant(0.001)))

# finally add the output layer
layers.append(tf.keras.layers.Dense(
    10, kernel_initializer=tf.initializers.RandomUniform(minval=-0.01,
                                                         maxval=0.01)))

lr = 0.1
for step in range(2000):
    img_batch, lbl_batch = mnist.next_batch()
    # I hear adding random noise to inputs helps with generalization!
    img_batch = img_batch + tf.random.normal(tf.shape(img_batch), stddev=4)
    with tf.GradientTape() as tape:
        # here we just run all the layers in sequence via a for-loop
        out = img_batch
        for layer in layers:
            out = layer(out)
        xent = tf.reduce_mean(tf.nn.sparse_softmax_cross_entropy_with_logits(
            logits=out, labels=lbl_batch))

    weights = [var for l in layers for var in l.trainable_variables]
    grads = tape.gradient(xent, weights)
    for grad, var in zip(grads, weights):
        var.assign_sub(lr*grad)

    with train_writer.as_default():
      tf.summary.histogram("Logits", out, step=step)
      tf.summary.histogram("Weights", weights[0], step=step)
      tf.summary.histogram("Weights_2", weights[2], step=step)
      tf.summary.histogram("Gradient", tf.norm(grads[0]), step=step)
      tf.summary.histogram("Gradient_2", tf.norm(grads[2]), step=step)

    if not step % 100:
        preds = tf.argmax(out, axis=1, output_type=tf.int32)
        acc = tf.reduce_mean(tf.cast(tf.equal(preds, lbl_batch), tf.float32))
        print("Loss: {} Accuracy: {}".format(xent, acc))
        with train_writer.as_default():
          tf.summary.scalar("Gradient Scalar", tf.norm(grads[0]), step=step)
          tf.summary.scalar("Loss", xent, step=step)
          tf.summary.scalar("Accuracy", acc, step=step)
          tf.summary.image("input", tf.reshape(img_batch, [-1, 28, 28, 1]), step=step)

out = mnist.test_data
for layer in layers:
    out = layer(out)
test_preds = tf.argmax(out, axis=1, output_type=tf.int32)
acc = tf.reduce_mean(tf.cast(tf.equal(test_preds, mnist.test_labels), tf.float32))
print("Final test accuracy: {}".format(acc))


Loss: 2.302534580230713 Accuracy: 0.109375
Loss: 2.303661346435547 Accuracy: 0.1015625
Starting new epoch...
Loss: 2.298006057739258 Accuracy: 0.140625
Loss: 2.3002471923828125 Accuracy: 0.14453125
Starting new epoch...
Loss: 2.2993035316467285 Accuracy: 0.12109375
Loss: 2.2968251705169678 Accuracy: 0.15625
Starting new epoch...
Loss: 2.296830415725708 Accuracy: 0.125
Loss: 2.295828342437744 Accuracy: 0.125
Loss: 2.3018577098846436 Accuracy: 0.08203125
Starting new epoch...
Loss: 2.2577662467956543 Accuracy: 0.20703125
Loss: 2.214202642440796 Accuracy: 0.1640625
Starting new epoch...
Loss: 2.2016892433166504 Accuracy: 0.1875
Loss: 2.049591064453125 Accuracy: 0.2734375
Starting new epoch...
Loss: 2.069967269897461 Accuracy: 0.2265625
Loss: 2.016172409057617 Accuracy: 0.2109375
Loss: 2.0664947032928467 Accuracy: 0.28515625
Starting new epoch...
Loss: 2.142005205154419 Accuracy: 0.25
Loss: 2.032130479812622 Accuracy: 0.2578125
Starting new epoch...
Loss: 2.0338919162750244 Accuracy: 0.300

Fail 5

Since the weights are too small and since there's an activation function also at the output layers there doesnt seems to be change in the gradient and also the logits seems to be between 0 and 0.125. Due to which there's not much change in loss as well. 
So to solve this maybe we can increase the range of weights and the model will learn to classify or by not changing the weight and removing activation function from the output layer.

In [12]:

logdir = os.path.join("logs", "fail" + str(time.time()))
train_writer = tf.summary.create_file_writer(os.path.join(logdir, "train"))
test_writer = tf.summary.create_file_writer(os.path.join(logdir, "test"))

# define the model first, from input to output

# let's use fewer layers...
n_units = 100
n_layers = 2

# just set up a "chain" of hidden layers
layers = []
for layer in range(n_layers):
    layers.append(tf.keras.layers.Dense(
        n_units, activation=tf.nn.relu,
        kernel_initializer=tf.initializers.RandomUniform(minval=-0.01,
                                                         maxval=0.01),
        bias_initializer=tf.initializers.constant(0.001)))

# finally add the softmax output layer :))
layers.append(tf.keras.layers.Dense(
    10, activation=tf.nn.softmax,
    kernel_initializer=tf.initializers.RandomUniform(minval=-0.01,
                                                     maxval=0.01)))

lr = 0.1
for step in range(2000):
    img_batch, lbl_batch = mnist.next_batch()
    with tf.GradientTape() as tape:
        # here we just run all the layers in sequence via a for-loop
        out = img_batch
        for layer in layers:
            out = layer(out)
        xent = tf.reduce_mean(tf.nn.sparse_softmax_cross_entropy_with_logits(
            logits=out, labels=lbl_batch))

    weights = [var for l in layers for var in l.trainable_variables]
    grads = tape.gradient(xent, weights)
    for grad, var in zip(grads, weights):
        var.assign_sub(lr*grad)

    with train_writer.as_default():
      tf.summary.histogram("Logits", out, step=step)
      tf.summary.histogram("Weights_0", weights[0], step=step)
      tf.summary.histogram("Weights_2", weights[2], step=step)
      tf.summary.histogram("Gradient_0", tf.norm(grads[0]), step=step)
      tf.summary.histogram("Gradient_2", tf.norm(grads[2]), step=step)

    if not step % 100:
        preds = tf.argmax(out, axis=1, output_type=tf.int32)
        acc = tf.reduce_mean(tf.cast(tf.equal(preds, lbl_batch), tf.float32))
        print("Loss: {} Accuracy: {}".format(xent, acc))
        with train_writer.as_default():
          tf.summary.scalar("Gradient Scalar", tf.norm(grads[0]), step=step)
          tf.summary.scalar("Loss", xent, step=step)
          tf.summary.scalar("Accuracy", acc, step=step)
          tf.summary.image("input", tf.reshape(img_batch, [-1, 28, 28, 1]), step=step)

out = mnist.test_data
for layer in layers:
    out = layer(out)
test_preds = tf.argmax(out, axis=1, output_type=tf.int32)
acc = tf.reduce_mean(tf.cast(tf.equal(test_preds, mnist.test_labels), tf.float32))
print("Final test accuracy: {}".format(acc))


Loss: 2.3025882244110107 Accuracy: 0.1171875
Loss: 2.3025808334350586 Accuracy: 0.09375
Loss: 2.302629232406616 Accuracy: 0.09375
Starting new epoch...
Loss: 2.3024494647979736 Accuracy: 0.125
Loss: 2.3022384643554688 Accuracy: 0.1171875
Starting new epoch...
Loss: 2.302619218826294 Accuracy: 0.10546875
Loss: 2.302471160888672 Accuracy: 0.1015625
Starting new epoch...
Loss: 2.3025641441345215 Accuracy: 0.09765625
Loss: 2.301866054534912 Accuracy: 0.14453125
Loss: 2.3024425506591797 Accuracy: 0.09765625
Starting new epoch...
Loss: 2.302309036254883 Accuracy: 0.1015625
Loss: 2.3028388023376465 Accuracy: 0.078125
Starting new epoch...
Loss: 2.302560329437256 Accuracy: 0.09765625
Loss: 2.301874876022339 Accuracy: 0.12890625
Starting new epoch...
Loss: 2.302546501159668 Accuracy: 0.109375
Loss: 2.301786184310913 Accuracy: 0.109375
Loss: 2.3021011352539062 Accuracy: 0.11328125
Starting new epoch...
Loss: 2.3013601303100586 Accuracy: 0.12890625
Loss: 2.302189826965332 Accuracy: 0.10546875
Sta

In [13]:
%load_ext tensorboard
%tensorboard --logdir logs/ 

Output hidden; open in https://colab.research.google.com to view.

In [0]:
def loss(logits, labels):
  return tf.reduce_mean(tf.nn.sparse_softmax_cross_entropy_with_logits(
            logits=logits, labels=labels))

In [0]:
class MLP_Model(object):
  def __init__(self):

    self.W = tf.Variable(tf.random.uniform(shape=[784,300], minval=-0.1, maxval=0.1, dtype=np.float32))
    self.b = tf.Variable(np.zeros(300, dtype=np.float32))
#    self.b = tf.Variable(tf.random.uniform(shape=[20], minval=0, maxval=1, dtype=np.float32))


    self.W2 = tf.Variable(tf.random.uniform(shape=[300,200], minval=-0.1, maxval=0.1, dtype=np.float32))
    self.b2 = tf.Variable(np.zeros(200, dtype=np.float32))
#    self.b2 = tf.Variable(tf.random.uniform(shape=[10], minval=0, maxval=1, dtype=np.float32))

    self.W3 = tf.Variable(tf.random.uniform(shape=[200,10], minval=-0.1, maxval=0.1, dtype=np.float32))
    self.b3 = tf.Variable(np.zeros(10, dtype=np.float32))

    self.loss = 0.0
    self.accuracy = 0.0

  def train(self, inputs, outputs, learning_rate):


    with tf.GradientTape() as t:
      # Hidden layer
      l1 = tf.add(tf.matmul(inputs, self.W), self.b)
      l1_op = tf.nn.relu(l1)

      # Hidden layer 2
      l2 = tf.add(tf.matmul(l1_op, self.W2), self.b2)
      l2_op = tf.nn.relu(l2)

      #Output Layer
      l3 = tf.add(tf.matmul(l2_op, self.W3), self.b3)
      y_pred = tf.nn.softmax(l3)

      #logits = tf.matmul(inputs, self.W) + self.b
      self.loss = loss(y_pred, outputs)

    dW3, db3, dW2, db2, dW, db = t.gradient(self.loss, [self.W3, self.b3, self.W2, self.b2, self.W, self.b])
    self.W3.assign_sub(learning_rate * dW3)
    self.b3.assign_sub(learning_rate * db3)

    self.W2.assign_sub(learning_rate * dW2)
    self.b2.assign_sub(learning_rate * db2)

    self.W.assign_sub(learning_rate * dW)
    self.b.assign_sub(learning_rate * db)

    preds = tf.argmax(y_pred, axis=1, output_type=tf.int32)
    self.accuracy = tf.reduce_mean(tf.cast(tf.equal(preds, outputs),
                             tf.float32))

In [16]:
(train_imgs, train_lbls), (test_imgs, test_lbls) = tf.keras.datasets.mnist.load_data()
train_imgs = (train_imgs.astype(np.float32) / 255.).reshape((-1, 784))
train_lbls = train_lbls.astype(np.int32)
test_imgs = (test_imgs.astype(np.float32) / 255.).reshape((-1, 784))
test_lbls = test_lbls.astype(np.int32)


mlp_model = MLP_Model()

batch_size = 128

train_data = tf.data.Dataset.from_tensor_slices((train_imgs, train_lbls))

train_data = train_data.repeat(3)
train_data = train_data.batch(batch_size)
train_data = train_data.shuffle(train_imgs.shape[0])

for step, batch_features in enumerate(train_data):
  
  #import ipdb; ipdb.set_trace()   # For Debugging
  mlp_model.train(batch_features[0], batch_features[1], learning_rate=0.1)
  if not step % 100:
    print('Step %2d: loss=%2.5f, accuracy=%2.5f' %
        (step, mlp_model.loss, mlp_model.accuracy))

Step  0: loss=2.30143, accuracy=0.10156
Step 100: loss=2.17419, accuracy=0.42188
Step 200: loss=1.90240, accuracy=0.65625
Step 300: loss=1.85567, accuracy=0.64844
Step 400: loss=1.74045, accuracy=0.74219
Step 500: loss=1.72050, accuracy=0.75000
Step 600: loss=1.78056, accuracy=0.68750
Step 700: loss=1.73316, accuracy=0.74219
Step 800: loss=1.69512, accuracy=0.77344
Step 900: loss=1.72175, accuracy=0.73438
Step 1000: loss=1.74319, accuracy=0.71875
Step 1100: loss=1.77334, accuracy=0.68750
Step 1200: loss=1.66378, accuracy=0.82031
Step 1300: loss=1.68686, accuracy=0.78125
Step 1400: loss=1.62514, accuracy=0.83594


In [0]:
test_data = tf.data.Dataset.from_tensor_slices((test_imgs, test_lbls))
test_data = test_data.batch(batch_size)


In [18]:
count = 0
acc = 0
for data in test_data:
  test_preds_h1 = tf.matmul(data[0], mlp_model.W) + mlp_model.b
  test_preds_h2 = tf.matmul(test_preds_h1, mlp_model.W2) + mlp_model.b2
  test_preds = tf.argmax(tf.matmul(test_preds_h2, mlp_model.W3) + mlp_model.b3, axis=1,
                        output_type=tf.int32)
  acc += tf.reduce_mean(tf.cast(tf.equal(test_preds, data[1]),
                              tf.float32))
  count += 1

print(acc/count)

tf.Tensor(0.82921284, shape=(), dtype=float32)


Shuffle,Batch,Repeat Ordering

1. Batch, Shuffle, Repeat - This ordering will create batches of dataset first then shuffle the batches and repeat those data set in the shuffled order.

  *   Training Accuracy - 78.9%
  *   Test Accuracy - 82.5%

2. Batch, Repeat, Shuffle - This first creates batches, and then repeat it and then shuffles the data in dataset.

  *   Training Accuracy - 89.8%
  *   Test Accuracy - 88.7%

3. Shuffle, Batch, Repeat - This first shuffles the data in dataset, and then create the batches of data and then repeats it.

  *   Training Accuracy - 86.7%
  *   Test Accuracy - 84.03%

4. Shuffle, Repeat, Batch - This first shuffles the data and then repeat those data and then make batches of it.

  *   Training Accuracy - 85.9%
  *   Test Accuracy - 80.7%

5. Repeat, Shuffle, Batch - First you repeat the data and shuffle it and make batches of it.

  *   Training Accuracy - 89.8%
  *   Test Accuracy - 83.8%

6. Repeat, Batch, Shuffle - First you repeat the data and make batches of it and then shuffle it.

  *   Training Accuracy - 83.5%
  *   Test Accuracy - 82.9%

I feel the sensible ordering will be to first Shuffle the dataset then makes Batches and Repeat 